In [134]:
from scipy.io import wavfile
import IPython
import numpy as np
import ffmpy
import wave
import numpy as np

In [68]:
rate1, data1 = wavfile.read("01.wav")
rate2, data2 = wavfile.read("24.wav")

IPython.display.Audio(data=data1, rate=rate1)


In [69]:
IPython.display.Audio(data=data2, rate=rate2)

## Volume 

In [91]:
from pydub import AudioSegment
from pydub.playback import play

song = AudioSegment.from_wav("01.wav")
song_10_db_quieter = song - 50
play(song_10_db_quieter)

song = AudioSegment.from_wav("01.wav")
song_10_db_quieter = song + 50
play(song_10_db_quieter)


## Speed

In [111]:
rate1, data1 = wavfile.read("01.wav")
rate2, data2 = wavfile.read("24.wav")

#0.5 TIMES SLOWER
ff = ffmpy.FFmpeg(inputs={"01.wav": None}, outputs={"out1.wav": ["-filter:a", "atempo=0.5"]})
ff.run()
#1.5 TIMES FASTER
ff = ffmpy.FFmpeg(inputs={"01.wav": None}, outputs={"out2.wav": ["-filter:a", "atempo=1.5"]})
ff.run()

(None, None)

## Noise

In [124]:
def fftnoise(f):
    f = np.array(f, dtype="complex")
    Np = (len(f) - 1) // 2
    phases = np.random.rand(Np) * 2 * np.pi
    phases = np.cos(phases) + 1j * np.sin(phases)
    f[1 : Np + 1] *= phases
    f[-1 : -1 - Np : -1] = np.conj(f[1 : Np + 1])
    return np.fft.ifft(f).real


def band_limited_noise(min_freq, max_freq, samples=1024, samplerate=1):
    freqs = np.abs(np.fft.fftfreq(samples, 1 / samplerate))
    f = np.zeros(samples)
    f[np.logical_and(freqs >= min_freq, freqs <= max_freq)] = 1
    return fftnoise(f)


In [125]:
noise_len = 19 # seconds
noise = band_limited_noise(min_freq=1000, max_freq = 20000, samples=len(data2), samplerate=rate2)*10
noise_clip = noise[:rate2*noise_len]
audio_clip_band_limited = data2+noise

In [126]:
IPython.display.Audio(data=audio_clip_band_limited, rate=rate2)

## Frequncy 

In [147]:
fr = 20
shift = 1000//fr  # shifting 100 Hz

wr = wave.open('24.wav', 'r')
# Set the parameters for the output file.
par = list(wr.getparams())
par[3] = 0  # The number of samples will be set by writeframes.
par = tuple(par)
ww = wave.open('pitch1.wav', 'w')
ww.setparams(par)


sz = wr.getframerate()//fr  # Read and process 1/fr second at a time.
# A larger number for fr means less reverb.
c = int(wr.getnframes()/sz)  # count of the whole file
for num in range(c):
    da = np.fromstring(wr.readframes(sz), dtype=np.int16)
    left, right = da[0::2], da[1::2]  # left and right channel
    lf, rf = np.fft.rfft(left), np.fft.rfft(right)
    lf, rf = np.roll(lf, shift), np.roll(rf, shift)
    lf[0:shift], rf[0:shift] = 0, 0
    nl, nr = np.fft.irfft(lf), np.fft.irfft(rf)
    ns = np.column_stack((nl, nr)).ravel().astype(np.int16)
    ww.writeframes(ns.tostring())
    

wr.close()
ww.close()
    

/Users/ppriyank/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:17: DeprecationWarning: The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead


In [150]:
import librosa
y, sr = librosa.load('24.wav', sr=16000) # y is a numpy array of the wav file, sr = sample rate
y_shifted = librosa.effects.pitch_shift(y, sr, n_steps=4)
librosa.write_wav("temp.wav", y_shifted, sr)

AttributeError: module 'librosa' has no attribute 'write_wav'